In [8]:
from skewPy import SkewT
import matplotlib.pyplot as plt
import numpy as np
import seaborn as sns
import pandas as pd
import glob

plt.close('all')

# Main folder where the reading is done; creates list of all current soundings
read_folder = '/Volumes/cruiseshare/Soundings/Thompson/edt/' # filepath to cruiseshare
file_list = sorted(glob.glob(read_folder + '*'))
print('List of soundings: ', file_list)
print('Most current sounding: ', file_list[-1])

# Read the most recent one
# I added some features; init_plot is 1 if you want it to make a plot when you create a 
# sounding, and 0 if you don't want it to plot.

# For Palau and other data, date_to_read feature allows you to select a particular day 
# from a data file days to plot.
S1 = SkewT.Sounding(filename=file_list[-1], fmt='PISTON_EDT', init_plot=1)


List of soundings:  ['/Volumes/cruiseshare/Soundings/Thompson/edt/edt_20180820_2335.txt', '/Volumes/cruiseshare/Soundings/Thompson/edt/edt_20180821_0530.txt', '/Volumes/cruiseshare/Soundings/Thompson/edt/edt_20180821_1235.txt', '/Volumes/cruiseshare/Soundings/Thompson/edt/edt_20180821_1733.txt', '/Volumes/cruiseshare/Soundings/Thompson/edt/edt_20180821_2333.txt', '/Volumes/cruiseshare/Soundings/Thompson/edt/edt_20180822_0523.txt', '/Volumes/cruiseshare/Soundings/Thompson/edt/edt_20180822_1128.txt', '/Volumes/cruiseshare/Soundings/Thompson/edt/edt_20180822_1724.txt', '/Volumes/cruiseshare/Soundings/Thompson/edt/edt_20180822_2328.txt', '/Volumes/cruiseshare/Soundings/Thompson/edt/edt_20180823_0226.txt', '/Volumes/cruiseshare/Soundings/Thompson/edt/edt_20180823_0526.txt', '/Volumes/cruiseshare/Soundings/Thompson/edt/edt_20180823_0827.txt', '/Volumes/cruiseshare/Soundings/Thompson/edt/edt_20180823_1128.txt', '/Volumes/cruiseshare/Soundings/Thompson/edt/edt_20180823_1426.txt', '/Volumes/cru

In [9]:
# Use to plot multiple soundings on the same plot; the indexing on files_list
# within the for loop controls what is displayed. Need to update to have legend
# and more robust color scheme, etc.

S1 = SkewT.Sounding(data={}, fmt='PISTON_EDT')
#S1.make_skewt_axes()
data_set = ()
date_list = ()

clrs = sns.color_palette('colorblind', len(file_list))

for file_name,idx in zip(file_list, np.arange(len(file_list))):
    S1.readfile(file_name)
    #S1.add_profile(color=clrs[-idx], bloc=.6 + .2*idx, bcol=clrs[-idx])
    data_set = np.append(data_set, S1.data)
    date_list = np.append(date_list, S1.sounding_date)



In [10]:
# Function which takes a dictionary data_in and interpolate a key "data_str" onto heights
# "goal_hghts". Might update to have automatically cycle through dictionary keys rather than
# take data_str, but not too many variables of interest to read
def interp_all(data_str, goal_hghts, data_in):
    data_out = np.empty([len(goal_hghts), len(data_in)])
    for i in range(len(data_in)):
        #print(data_in[i]['hght'])
        #print(data_in[i][data_str])
        data_out[:,i] = np.interp(goal_hghts, data_in[i]['hght'], data_in[i][data_str])
        #print(data_in[i]['hght'].max())
        #print(goal_hghts>data_in[i]['hght'].max())
        data_out[np.where(goal_hghts>data_in[i]['hght'].max()), i] = np.nan
    return(data_out)

# Sets up goal heights up to 21km and interpolate tempa nd dewpt
z = np.linspace(0, 17000, 2000)

# Does the interpolation
temp = interp_all('temp', z, data_set)
dwpt = interp_all('dwpt', z, data_set)
pres = interp_all('pres', z, data_set)


# Calculates zonal and meridional wind from the speed and direction
u = np.empty([len(z), len(data_set)])
v = np.empty(u.shape)

# More interpolation
for i in range(len(data_set)):
    utemp = data_set[i]['sknt']*np.cos(np.radians(270-data_set[i]['drct']))
    vtemp = data_set[i]['sknt']*np.sin(np.radians(270-data_set[i]['drct']))
    utemp = np.interp(z, data_set[i]['hght'], utemp)
    vtemp = np.interp(z, data_set[i]['hght'], vtemp)
    utemp[np.where(z>data_set[i]['hght'].max())] = np.nan
    vtemp[np.where(z>data_set[i]['hght'].max())] = np.nan
    u[:,i] = utemp
    v[:,i] = vtemp
#print(u)

# Calculates relative humidity
relh = SkewT.RH(temp, dwpt)

pres = np.nanmean(pres, 1)

In [11]:
print(pres)

[ 1008.79904762  1008.17488289  1007.21054407 ...,    93.54822024
    93.4061567     93.27231672]


In [12]:
# Makes plots of time series of data

# Starts with some temperature info

fig = plt.figure()

ax1 = fig.add_subplot(3,1,1)
ax2 = fig.add_subplot(3,1,2)
ax3 = fig.add_subplot(3,1,3)

# Main temperature
cf = ax1.contourf(date_list, z, temp, cmap='RdBu_r')
plt.colorbar(cf, ax=ax1)

ax1.set_title('Temperature (C)')

# Cold point tropopause
ax2.plot(date_list, np.min(temp, 0))
ax2.set_title('Cold point tropopause (C)')

# Finds the melting level and plots
melting_level = np.empty(len(data_set))
for i in range(len(data_set)):
          melting_level[i] = data_set[i]['hght'][np.argmin(abs(data_set[i]['temp']-0))]

ax3.plot(date_list, melting_level/1000)
ax3.set_title('Melting Level (km)')

fig.tight_layout()
plt.show()

In [13]:
# Other diagnostics on a plot
fig = plt.figure()

ax1 = fig.add_subplot(4,1,1)
ax2 = fig.add_subplot(4,1,2)
ax3 = fig.add_subplot(4,1,3)
ax4 = fig.add_subplot(4,1,4)


# Finds the temperature anomaly
temp_anom = np.empty(temp.shape)
for i in range(temp.shape[1]):
    temp_anom[:,i] = temp[:, i] - np.nanmean(temp,1)
    
cf = ax1.contourf(date_list, z, temp_anom,np.arange(-2, 2, .25), cmap='RdBu_r', extend='both')
plt.colorbar(cf, ax=ax1)
ax1.set_yticks([0,5000, 10000, 15000])
ax1.set_yticklabels([0,5000, 10000, 15000])
ax1.set_title('Temperature Anomaly (C)')

# Zonal and meridional wind
cf = ax2.contourf(date_list, z, u, np.arange(-30, 30, 5), cmap='RdBu_r', extend='both')
ax2.set_title('Zonal wind (knots)')
ax2.set_yticks([0,5000, 10000, 15000])
ax2.set_yticklabels([0,5000, 10000, 15000])
plt.colorbar(cf, ax=ax2)

cf = ax3.contourf(date_list, z, v, np.arange(-30, 30, 5), cmap='RdBu_r', extend='both')
ax3.set_title('Meridional wind (knots)')
ax3.set_yticks([0,5000, 10000, 15000])
ax3.set_yticklabels([0,5000, 10000, 15000])
plt.colorbar(cf, ax=ax3)

# Relative humidity

# Finds the relative humidity anomaly and plots
relh_anom = np.empty(relh.shape)
for i in range(relh.shape[1]):
    relh_anom[:,i] = relh[:, i] - np.nanmean(relh, 1)
    
cf = ax4.contourf(date_list, z, relh_anom , cmap='BrBG')
ax4.set_title('Relative Humidity Anomaly (%)')
plt.colorbar(cf, ax=ax4)
ax4.set_yticks([0,5000, 10000, 15000])
ax4.set_yticklabels([0,5000, 10000, 15000])
fig.tight_layout()
plt.show()


In [14]:
# This take the mean of the current soundings and plots; shouldn't be too hard to adapt
# for means over certain periods.
Smean = {}
for key in S1.data.keys():
    #print(key)
    for i in range(len(data_set)):
        tmp = data_set[i][key]
        tmp = np.interp(z, data_set[i]['hght'], data_set[i][key])
        #print(temp)
        if i == 0:
            Smean[key] = tmp
        else:
            Smean[key] = (Smean[key] + tmp)/2

mean_sounding = SkewT.Sounding(data=Smean,)
mean_sounding.plot_skewt(title='Mean sounding',  imageout = True, imagename = 'test')

p_lcl =  946.807570329
lcl_height =  561.28064032
saving figure
